In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

In [8]:
from glob import glob
import xarray
import numpy
import dask
from e3smplot.e3sm_utils import get_data

In [4]:
data_path = '/global/cfs/cdirs/e3sm/terai/SCREAM/DYAMOND2/Output/20201127/regridded'
p_files = sorted(glob(f'{data_path}/*.eam.h4.*.nc'))
t_files = sorted(glob(f'{data_path}/*.eam.h6.*.nc'))

In [7]:
ds_p = xarray.open_mfdataset(p_files, drop_variables=('P3_input_dim', 'P3_output_dim'), chunks={'time': 1, 'lev': 1})
ds_t = xarray.open_mfdataset(t_files, drop_variables=('P3_input_dim', 'P3_output_dim'), chunks={'time': 1, 'lev': 1})

In [53]:
p = get_data(ds_p, 'PMID')
t = get_data(ds_t, 'T')

In [54]:
levels = (200, 300, 400, 500, 600, 700, 800, 850, 925, 1000)

In [55]:
levels = xarray.DataArray(
    numpy.array(levels), dims=('level'), attrs={'long_name': 'Pressure', 'units': 'hPa'}
)
t_p = xarray.DataArray(
    dask.array.zeros([t.time.size, len(levels), t.lat.size, t.lon.size], chunks=(1, len(levels), t.lat.size, t.lon.size))
)

In [56]:
levels, *__ = xarray.broadcast(
    levels, p.isel(lev=0)
)

In [57]:
levels = levels.transpose('time', 'level', 'lat', 'lon')

In [58]:
levels.dims

('time', 'level', 'lat', 'lon')

In [62]:
t.data = t.data.rechunk((1, t.lev.size, t.lat.size, t.lon.size))
p.data = p.data.rechunk((1, p.lev.size, p.lat.size, p.lon.size))
t_p.data = xarray.apply_ufunc(
    numpy.interp, levels, p, t,
    exclude_dims=set(('lev',)),
    input_core_dims=[[], ['lev',], ['lev',]],
    dask='parallelized',
    vectorize=True,
)

/global/homes/b/bhillma/.conda/envs/e3smplot/lib/python3.8/site-packages/dask/array/gufunc.py:430: PerformanceWarning: Increasing number of chunks by factor of 32
  tmp = blockwise(  # First try to compute meta


In [ ]:
print('done')